In [1]:
from tqdm import tqdm
import pandas as pd
from ergochemics import mapping
from typing import List
import multiprocessing
import os
multiprocessing.set_start_method("fork", force=True)

In [2]:
def make_rule_id(n: int, prefix: str = "rule", width: int = 4) -> str:
    """
    Convert an integer into a zero-padded rule ID of the form 'rule0001'.

    Args:
        n (int): The integer to convert.
        prefix (str): Optional prefix before the number. Defaults to "rule".
        width (int): Zero-padding width. Defaults to 4.

    Returns:
        str: Formatted rule ID (e.g., 'rule0004').
    """
    if n < 1:
        raise ValueError("Input must be >= 1.")
    return f"{prefix}{n:0{width}d}"


In [3]:
# extract and create a list of all minimal operators' SMARTS strings
gen_rxn_operators_df = pd.read_csv("../data/raw/JN1224MIN_rules.tsv", delimiter='\t')
gen_rxn_operators_list: List[str] = gen_rxn_operators_df["SMARTS"].to_list()

# extract and create a list of all unmapped MetaCyc reactions
EnzymeMap_MetaCyc_rxns_df = pd.read_csv("../data/raw/enzymemap_MetaCyc_processed.csv")
EnzymeMap_MetaCyc_rxns_unmapped: List[str] = EnzymeMap_MetaCyc_rxns_df["unmapped"].to_list()

# remove all hydrogen ions from rxn strings so that they can be mapped by Stefan's ergochemics
EnzymeMap_MetaCyc_rxns_cleaned: List[str] = []

for rxn in EnzymeMap_MetaCyc_rxns_unmapped:
    rxn = rxn.replace(".[H+]","").replace("[H+].","")
    EnzymeMap_MetaCyc_rxns_cleaned.append(rxn)

In [4]:
def map_single_reaction(args):
    """(index, rxn, operator_list) → (index, mapped_ops)"""
    idx, rxn, gen_rxn_operators_list = args

    mapped_ops = []
    try:
        for i, operator in enumerate(gen_rxn_operators_list):
            try:
                mapped_rxn = mapping.operator_map_reaction(rxn=rxn, operator=operator)
                if mapped_rxn.did_map:
                    mapped_ops.append(make_rule_id(i+1))
            except Exception:
                pass
    except Exception as e:
        return idx, f"__WORKER_FAILED__: {repr(e)}"

    return idx, mapped_ops


# ---- MAIN ----
rxns = EnzymeMap_MetaCyc_rxns_cleaned
tasks = [(i, rxn, gen_rxn_operators_list) for i, rxn in enumerate(rxns)]

results = [None] * len(tasks)

with multiprocessing.Pool(os.cpu_count()) as p:
    for idx, mapped_ops in tqdm(
        p.imap_unordered(map_single_reaction, tasks),
        total=len(tasks),
        desc="Mapping reactions",
    ):
        results[idx] = mapped_ops

all_mapped_operators = results

Mapping reactions:   0%|          | 0/4581 [00:00<?, ?it/s][18:07:20] Initializing MetalDisconnector
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing MetalDisconnector
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing Normalizer
[18:07:20] Initializing Normalizer
[18:07:20] Running Normalizer
[18:07:20] Running Normalizer
[18:07:20] Initializing MetalDisconnector
[18:07:20] Initializing MetalDisconnector
[18:07:20] Initializing MetalDisconnector
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing MetalDisconnector
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing MetalDisconnector
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing MetalDisconnector
[18:07:20] Initializing Normalizer
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing Normalizer
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing Normalizer
[18:07:20] Running MetalDisconnector
[18:07:20] Initializing Normalizer
[18:07:20] Running Normalizer
[18:07:20

Error parsing tautomerized reactant for: C[S+](CCC(N)C(=O)O)CC1OC(n2cnc3c(N)ncnc32)C(O)C1O.Cn1cnc2[nH]c(=O)[nH]c(=O)c21>>Cn1cnc2c1c(=O)[nH]c(=O)n2C.Nc1ncnc2c1ncn2C1OC(CSCCC(N)C(=O)O)C(O)C1O


[18:37:21] Can't kekulize mol.  Unkekulized atoms: 2 4 5 11


Error parsing tautomerized reactant for: C[S+](CCC(N)C(=O)O)CC1OC(n2cnc3c(N)ncnc32)C(O)C1O.Cn1cnc2[nH]c(=O)[nH]c(=O)c21>>Cn1cnc2c1c(=O)[nH]c(=O)n2C.Nc1ncnc2c1ncn2C1OC(CSCCC(N)C(=O)O)C(O)C1O


[18:37:21] Can't kekulize mol.  Unkekulized atoms: 2 4 5 11


...

[19:55:55] Can't kekulize mol.  Unkekulized atoms: 1 2 3 4 5 8 12 27 28 29


Error parsing tautomerized reactant for: Cc1cc2nc3c(=O)[nH]c(=O)nc-3n(CC(O)C(O)C(O)COP(=O)(O)O)c2cc1C.O>>Cc1cc2nc3c(=O)[nH]c(=O)nc-3n(CC(O)C(O)C(O)CO)c2cc1C.O=P(O)(O)O


[19:55:55] Can't kekulize mol.  Unkekulized atoms: 1 2 3 4 5 8 12 27 28 29


Error parsing tautomerized reactant for: Cc1cc2nc3c(=O)[nH]c(=O)nc-3n(CC(O)C(O)C(O)COP(=O)(O)O)c2cc1C.O>>Cc1cc2nc3c(=O)[nH]c(=O)nc-3n(CC(O)C(O)C(O)CO)c2cc1C.O=P(O)(O)O


Mapping reactions:  67%|██████▋   | 3084/4581 [1:48:38<04:18,  5.78it/s][19:55:55] Initializing MetalDisconnector
[19:55:55] Running MetalDisconnector
[19:55:55] Initializing Normalizer
[19:55:55] Running Normalizer
[19:55:55] Initializing MetalDisconnector
[19:55:55] Running MetalDisconnector
[19:55:55] Initializing Normalizer
[19:55:55] Running Normalizer
[19:55:55] Initializing MetalDisconnector
[19:55:55] Running MetalDisconnector
[19:55:55] Initializing Normalizer
[19:55:55] Running Normalizer
[19:55:55] Initializing MetalDisconnector
[19:55:55] Running MetalDisconnector
[19:55:55] Initializing Normalizer
[19:55:55] Running Normalizer
[19:55:55] Initializing MetalDisconnector
[19:55:55] Running MetalDisconnector
[19:55:55] Initializing Normalizer
[19:55:55] Running Normalizer
[19:55:55] Initializing MetalDisconnector
[19:55:55] Running MetalDisconnector
[19:55:55] Initializing Normalizer
[19:55:55] Running Normalizer
[19:55:55] Initializing MetalDisconnector
[19:55:55] Running Met

In [7]:
EnzymeMap_MetaCyc_rxns_df["all_mapped_operators"] = all_mapped_operators

In [12]:
EnzymeMap_MetaCyc_rxns_df.head(3)

rxn_idx                                             mapped  \
0      903  [CH3:1][CH2:2][OH:3].[NH2:4][C:5](=[O:6])[c:7]...   
1      903  [CH3:1][CH:2]=[O:3].[H+].[NH2:4][C:5](=[O:6])[...   
2     2286  [H+].[NH2:1][C:2](=[O:3])[C:4]1=[CH:5][N:6]([C...   

                                            unmapped         orig_rxn_text  \
0  CCO.NC(=O)c1ccc[n+]([C@@H]2O[C@H](COP(=O)(O)OP...  ALCOHOL-DEHYDROG-RXN   
1  CC=O.NC(=O)C1=CN([C@@H]2O[C@H](COP(=O)(O)OP(=O...  ALCOHOL-DEHYDROG-RXN   
2  NC(=O)C1=CN([C@@H]2O[C@H](COP(=O)(O)OP(=O)(O)O...             RXN-10781   

                                                rule  rule_id  \
0  [#6:1]-[#8:2].[#6:3]1:[#6:4]:[#6:5]:[#6:6]:[#7...        1   
1  [#6:1]-[#8:2].[#6:3]1:[#6:4]:[#6:5]:[#6:6]:[#7...        1   
2  [#6:1]1=[#6:2]-[#7:3]-[#6:4]=[#6:5]-[#6:6]-1.[...        0   

            source   steps  quality  natural  organism protein_refs  \
0           direct  single      1.0      NaN       NaN           []   
1  direct reversed  single      1.0      NaN       NaN           []   
2           direct  single      1.0      NaN       NaN           []   

   protein_db   ec_num  all_mapped_operators  
0         NaN  1.1.1.1  [rule0002, rule0754]  
1         NaN  1.1.1.1  [rule0003, rule0753]  
2         NaN  1.1.1.1            [rule0003]

In [13]:
def get_top_operator(op_list):
    """
    Given a list like ['rule0002', 'rule0754'], return the one with
    the smallest integer value (e.g. 'rule0002').
    """
    if not op_list:
        return None  # or np.nan if you prefer

    # extract integer part: "rule0034" → 34
    nums = [int(op.replace("rule", "")) for op in op_list]

    # lowest rule number
    min_num = min(nums)

    # convert back to rule format
    return f"rule{min_num:04d}"


EnzymeMap_MetaCyc_rxns_df["top_mapped_operator"] = (
    EnzymeMap_MetaCyc_rxns_df["all_mapped_operators"]
    .apply(get_top_operator)
)


In [14]:
EnzymeMap_MetaCyc_rxns_df

rxn_idx                                             mapped  \
0         903  [CH3:1][CH2:2][OH:3].[NH2:4][C:5](=[O:6])[c:7]...   
1         903  [CH3:1][CH:2]=[O:3].[H+].[NH2:4][C:5](=[O:6])[...   
2        2286  [H+].[NH2:1][C:2](=[O:3])[C:4]1=[CH:5][N:6]([C...   
3        2320  [H+].[NH2:1][C:2](=[O:3])[C:4]1=[CH:5][N:6]([C...   
4        2324  [CH3:1][O:2][c:3]1[cH:4][c:5]([C@@H:6]([OH:7])...   
...       ...                                                ...   
4576     1711  [CH3:1][C:2]([CH3:3])([CH2:4][O:5][P:6](=[O:7]...   
4577     1711  [CH3:1][C:2]([CH3:3])([CH2:4][O:5][P:6](=[O:7]...   
4578     3419  [NH2:1][c:2]1[cH:3][cH:4][cH:5][cH:6][cH:7]1.[...   
4579      818  [NH2:18][c:19]1[n:20][cH:21][n:22][c:23]2[c:24...   
4580     2164  [NH2:1][C:2](=[O:3])[c:4]1[n:5][cH:6][n:7]([C@...   

                                               unmapped  \
0     CCO.NC(=O)c1ccc[n+]([C@@H]2O[C@H](COP(=O)(O)OP...   
1     CC=O.NC(=O)C1=CN([C@@H]2O[C@H](COP(=O)(O)OP(=O...   
2     NC(=O)C1=CN([C@@H]2O[C@H](COP(=O)(O)OP(=O)(O)O...   
3     NC(=O)C1=CN([C@@H]2O[C@H](COP(=O)(O)OP(=O)(O)O...   
4     COc1cc([C@@H](O)CO)ccc1O.NC(=O)c1ccc[n+]([C@@H...   
...                                                 ...   
4576  CC(C)(COP(=O)([O-])OP(=O)([O-])OC[C@H]1O[C@@H]...   
4577  CC(C)(COP(=O)([O-])OP(=O)([O-])OC[C@H]1O[C@@H]...   
4578  Nc1ccccc1.Nc1ncnc2c1ncn2[C@@H]1O[C@H](COP(=O)(...   
4579  NC(=[NH2+])NCCC[C@H](NCCC(=O)[O-])C(=O)[O-].Nc...   
4580  NC(=O)c1ncn([C@@H]2O[C@H](COP(=O)([O-])[O-])[C...   

               orig_rxn_text  \
0       ALCOHOL-DEHYDROG-RXN   
1       ALCOHOL-DEHYDROG-RXN   
2                  RXN-10781   
3                  RXN-10911   
4                  RXN-10915   
...                      ...   
4576  MALATE--COA-LIGASE-RXN   
4577  MALATE--COA-LIGASE-RXN   
4578               RXN-14637   
4579             6.3.3.4-RXN   
4580               RXN-10066   

                                                   rule  rule_id  \
0     [#6:1]-[#8:2].[#6:3]1:[#6:4]:[#6:5]:[#6:6]:[#7...        1   
1     [#6:1]-[#8:2].[#6:3]1:[#6:4]:[#6:5]:[#6:6]:[#7...        1   
2     [#6:1]1=[#6:2]-[#7:3]-[#6:4]=[#6:5]-[#6:6]-1.[...        0   
3     [#6:1]1=[#6:2]-[#7:3]-[#6:4]=[#6:5]-[#6:6]-1.[...        0   
4     [#6:1]-[#8:2].[#6:3]1:[#6:4]:[#6:5]:[#6:6]:[#7...        1   
...                                                 ...      ...   
4576  [#16:1].[#6:2]-[#8:3].[#8:4]-[#15:5]>>[#6:2]-[...      828   
4577  [#16:1].[#6:2]-[#8:3].[#8:4]-[#15:5]>>[#6:2]-[...      828   
4578  [#6:1]-[#8:2].[#7:3].[#8:4]-[#15:5]>>[#6:1]-[#...      827   
4579  ([#7:1].[#6:2]-[#8:3]).[#8:4]-[#15:5]>>[#6:2]-...      842   
4580  [#6:1]-[#8:2].[#7:3].[#8:4]-[#15:5]>>[#6:1]-[#...      827   

               source   steps  quality  natural  organism protein_refs  \
0              direct  single      1.0      NaN       NaN           []   
1     direct reversed  single      1.0      NaN       NaN           []   
2              direct  single      1.0      NaN       NaN           []   
3              direct  single      1.0      NaN       NaN           []   
4              direct  single      1.0      NaN       NaN           []   
...               ...     ...      ...      ...       ...          ...   
4576           direct  single      1.0      NaN       NaN           []   
4577  direct reversed  single      1.0      NaN       NaN           []   
4578           direct  single      1.0      NaN       NaN           []   
4579           direct  single      1.0      NaN       NaN           []   
4580           direct  single      1.0      NaN       NaN           []   

      protein_db    ec_num                      all_mapped_operators  \
0            NaN   1.1.1.1                      [rule0002, rule0754]   
1            NaN   1.1.1.1                      [rule0003, rule0753]   
2            NaN   1.1.1.1                                [rule0003]   
3            NaN   1.1.1.1                      [rule0003, rule0348]   
4            NaN   1.1.1.1   